# Tensorflow Object Detection API and AWS Sagemaker

In this notebook, you will train and evaluate different models using the [Tensorflow Object Detection API](https://tensorflow-object-detection-api-tutorial.readthedocs.io/en/latest/) and [AWS Sagemaker](https://aws.amazon.com/sagemaker/). 

If you ever feel stuck, you can refer to this [tutorial](https://aws.amazon.com/blogs/machine-learning/training-and-deploying-models-using-tensorflow-2-with-the-object-detection-api-on-amazon-sagemaker/).

## Dataset

We are using the [Waymo Open Dataset](https://waymo.com/open/) for this project. The dataset has already been exported using the tfrecords format. The files have been created following the format described [here](https://tensorflow-object-detection-api-tutorial.readthedocs.io/en/latest/training.html#create-tensorflow-records). You can find data stored on [AWS S3](https://aws.amazon.com/s3/), AWS Object Storage. The images are saved with a resolution of 640x640.

In [1]:
%%capture
%pip install tensorflow_io sagemaker -U

In [2]:
import os
import sagemaker
from sagemaker.estimator import Estimator
from framework import CustomFramework

sagemaker.config INFO - Not applying SDK defaults from location: /etc/xdg/sagemaker/config.yaml
sagemaker.config INFO - Not applying SDK defaults from location: /home/ec2-user/.config/sagemaker/config.yaml


Save the IAM role in a variable called `role`. This would be useful when training the model.

In [3]:
role = sagemaker.get_execution_role()
print(role)

arn:aws:iam::038462780242:role/service-role/AmazonSageMaker-ExecutionRole-20240906T152680


In [4]:
# The train and val paths below are public S3 buckets created by Udacity for this project
inputs = {'train': 's3://cd2688-object-detection-tf2/train/', 
          'val': 's3://cd2688-object-detection-tf2/val/'} 

# Insert path of a folder in your personal S3 bucket to store tensorboard logs.
tensorboard_s3_prefix = 's3://object.detection.project/logs/'

## Container

To train the model, you will first need to build a [docker](https://www.docker.com/) container with all the dependencies required by the TF Object Detection API. The code below does the following:
* clone the Tensorflow models repository
* get the exporter and training scripts from the repository
* build the docker image and push it 
* print the container name

In [5]:
#%%bash

## clone the repo and get the scripts
#git clone https://github.com/tensorflow/models.git docker/models

## get model_main and exporter_main files from TF2 Object Detection GitHub repository
#cp docker/models/research/object_detection/exporter_main_v2.py source_dir 
#cp docker/models/research/object_detection/model_main_tf2.py source_dir

Cloning into 'docker/models'...


In [6]:
## build and push the docker image. This code can be commented out after being run once.
## This will take around 10 mins.
#image_name = 'tf2-object-detection'
#!sh ./docker/build_and_push.sh $image_name

WARNING! Your password will be stored unencrypted in /home/ec2-user/.docker/config.json.
Configure a credential helper to remove this warning. See
https://docs.docker.com/engine/reference/commandline/login/#credentials-store

Login Succeeded
Building image with name tf2-object-detection
[+] Building 0.0s (0/1)                                          docker:default
[+] Building 0.2s (1/2)                                          docker:default
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 1.01kB                                     0.0s
 => [internal] load metadata for docker.io/tensorflow/tensorflow:2.13.0-g  0.2s
[+] Building 0.3s (2/2)                                          docker:default
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 1.01kB                                     0.0s
 => [internal] load metadata for docker.io/tensorflow/tensorflow:2.13.0-

[+] Building 1.1s (4/15)                                         docker:default
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 1.01kB                                     0.0s
 => [internal] load metadata for docker.io/tensorflow/tensorflow:2.13.0-g  0.2s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 2B                                            0.0s
 => [ 1/11] FROM docker.io/tensorflow/tensorflow:2.13.0-gpu@sha256:b46767  0.8s
 => => resolve docker.io/tensorflow/tensorflow:2.13.0-gpu@sha256:b4676741  0.0s
 => => sha256:b4676741c491bff3d0f29c38c369281792c7d5c5bfa 4.08kB / 4.08kB  0.0s
 => => sha256:6bdca089cc382c11ef5675cf72232e58fbad3a8c7 11.79kB / 11.79kB  0.0s
 => => sha256:56e0351b98767487b3c411034be95479ed1710bb6 27.51MB / 27.51MB  0.5s
 => => sha256:20d547ab5eb53128ec992abaae1d1f5a15bfe39d7a1 7.94MB / 7.94MB  0.4s
 => => sha256:ece84004a3cd8e7689a2ff0b1a

[+] Building 1.5s (4/15)                                         docker:default
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 1.01kB                                     0.0s
 => [internal] load metadata for docker.io/tensorflow/tensorflow:2.13.0-g  0.2s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 2B                                            0.0s
 => [ 1/11] FROM docker.io/tensorflow/tensorflow:2.13.0-gpu@sha256:b46767  1.2s
 => => resolve docker.io/tensorflow/tensorflow:2.13.0-gpu@sha256:b4676741  0.0s
 => => sha256:b4676741c491bff3d0f29c38c369281792c7d5c5bfa 4.08kB / 4.08kB  0.0s
 => => sha256:6bdca089cc382c11ef5675cf72232e58fbad3a8c7 11.79kB / 11.79kB  0.0s
 => => sha256:56e0351b98767487b3c411034be95479ed1710bb6 27.51MB / 27.51MB  0.5s
 => => sha256:20d547ab5eb53128ec992abaae1d1f5a15bfe39d7a1 7.94MB / 7.94MB  0.4s
 => => sha256:ece84004a3cd8e7689a2ff0b1a

[+] Building 2.0s (4/15)                                         docker:default
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 2B                                            0.0s
 => [ 1/11] FROM docker.io/tensorflow/tensorflow:2.13.0-gpu@sha256:b46767  1.7s
 => => resolve docker.io/tensorflow/tensorflow:2.13.0-gpu@sha256:b4676741  0.0s
 => => sha256:b4676741c491bff3d0f29c38c369281792c7d5c5bfa 4.08kB / 4.08kB  0.0s
 => => sha256:6bdca089cc382c11ef5675cf72232e58fbad3a8c7 11.79kB / 11.79kB  0.0s
 => => sha256:56e0351b98767487b3c411034be95479ed1710bb6 27.51MB / 27.51MB  0.5s
 => => sha256:20d547ab5eb53128ec992abaae1d1f5a15bfe39d7a1 7.94MB / 7.94MB  0.4s
 => => sha256:ece84004a3cd8e7689a2ff0b1a1856a941e6cc31f 56.23MB / 56.23MB  1.7s
 => => sha256:b08eef4b90c81de27f73f4aa3522ac14ee1e1146db910e9 186B / 186B  0.5s
 => => extracting sha256:56e0351b98767487b3c411034be95479ed1710bb6be860db  1.0s
 => => sha256:de96f27d948755d7ed0557a213

[+] Building 2.5s (4/15)                                         docker:default
 => [ 1/11] FROM docker.io/tensorflow/tensorflow:2.13.0-gpu@sha256:b46767  2.2s
 => => sha256:20d547ab5eb53128ec992abaae1d1f5a15bfe39d7a1 7.94MB / 7.94MB  0.4s
 => => sha256:ece84004a3cd8e7689a2ff0b1a1856a941e6cc31f 56.23MB / 56.23MB  1.8s
 => => sha256:b08eef4b90c81de27f73f4aa3522ac14ee1e1146db910e9 186B / 186B  0.5s
 => => extracting sha256:56e0351b98767487b3c411034be95479ed1710bb6be860db  1.0s
 => => sha256:de96f27d948755d7ed0557a21364768e9d85eeabdd8ea7f 977B / 977B  0.6s
 => => sha256:0d0dce5452b7074590ad5dc15e49d40ea82eb5c2304ec6d 768B / 768B  0.6s
 => => sha256:aa315b7808f0b5e5badf02398e1f7ce1780952eda55 6.88kB / 6.88kB  0.6s
 => => sha256:18e62fb4b02bf94f08abbe9c472441cb487f759cc1 99.61MB / 2.52GB  2.2s
 => => sha256:5a1e96a5c562cfcd77e326f0822fe6ba9b7540a3041e480 435B / 435B  0.6s
 => => sha256:780a8581227d0b3707efa2d1327690624bd8e4aeb 32.19MB / 32.19MB  1.2s
 => => sha256:1eb5af93509e197319fe2b95e0

...

[+] Building 197.2s (15/16)                                      docker:default
 => => extracting sha256:1eb5af93509e197319fe2b95e0ecc382af70353a19e370c1  0.0s
 => => extracting sha256:2e482ebc3ac75f8549fcda5398d339c473b0b2513df3490d  0.0s
 => => extracting sha256:1b05b9c327ea3c1ab594685cbc6a2e81762def76f5a8cafe  0.8s
 => => extracting sha256:38fe50d989691442c8c2504bac7940994904fbded380b01  13.5s
 => => extracting sha256:ac042b037de7062fda11dbfb03be0a430305d912d14daf4a  0.0s
 => => extracting sha256:2009c4c4e2d5daeff2f37140e3885fc80ab003d778c5b1d5  0.0s
 => => extracting sha256:b1c3a97d184ade58e969736e2883b029917f5ce1d5d31ab3  0.0s
 => => extracting sha256:fe5937c77f3eb80423ea3bfdab80dcb93bf7f4063a12c5fd  0.0s
 => [internal] load build context                                          0.2s
 => => transferring context: 31.40MB                                       0.2s
 => [ 2/11] RUN apt-get update && apt-get install -y     git     gpg-age  27.6s
 => [ 3/11] COPY models/research/object_

[+] Building 197.8s (15/16)                                      docker:default
 => => extracting sha256:1eb5af93509e197319fe2b95e0ecc382af70353a19e370c1  0.0s
 => => extracting sha256:2e482ebc3ac75f8549fcda5398d339c473b0b2513df3490d  0.0s
 => => extracting sha256:1b05b9c327ea3c1ab594685cbc6a2e81762def76f5a8cafe  0.8s
 => => extracting sha256:38fe50d989691442c8c2504bac7940994904fbded380b01  13.5s
 => => extracting sha256:ac042b037de7062fda11dbfb03be0a430305d912d14daf4a  0.0s
 => => extracting sha256:2009c4c4e2d5daeff2f37140e3885fc80ab003d778c5b1d5  0.0s
 => => extracting sha256:b1c3a97d184ade58e969736e2883b029917f5ce1d5d31ab3  0.0s
 => => extracting sha256:fe5937c77f3eb80423ea3bfdab80dcb93bf7f4063a12c5fd  0.0s
 => [internal] load build context                                          0.2s
 => => transferring context: 31.40MB                                       0.2s
 => [ 2/11] RUN apt-get update && apt-get install -y     git     gpg-age  27.6s
 => [ 3/11] COPY models/research/object_

The push refers to repository [038462780242.dkr.ecr.us-east-1.amazonaws.com/tf2-object-detection]

c93ffcb6: Preparing 
83bca088: Preparing 
e4ef3eea: Preparing 
888e7bd5: Preparing 
726d6d6a: Preparing 
aec817eb: Preparing 
bf18a086: Preparing 
570cc5a3: Preparing 
cb009c90: Preparing 
4f0fe379: Preparing 
a40e4dcd: Preparing 
b5695a98: Preparing 
f0d116f4: Preparing 
2813a979: Preparing 
6e868aa5: Preparing 
136c7d36: Preparing 
891e0e76: Preparing 
ed848ac5: Preparing 
18b47754: Preparing 
91e05b94: Preparing 
e103257c: Preparing 
b25399cb: Preparing 
b667a965: Preparing 
6ad9c95e: Preparing 
b4e1ecd1: Preparing 
5c845fcf: Preparing 
a7216f78: Preparing 


e868aa5: Pushing  1.121GB/1.614GBPushing  229.7MB/4.636GB8b47754: Pushing  3.396GB/4.636GBPushing  1.075GB/4.636GBPushing  1.462GB/1.614GBPushing  2.056GB/4.636GBPushing  2.082GB/4.636GBPushing  2.305GB/4.636GBPushing  2.417GB/4.636GBPushing  2.772GB/4.636GBPushing  3.008GB/4.636GBPushing  3.297GB/4.636GB

8b47754: Pushed   4.646GB/4.636GBPushing  3.403GB/4.636GBPushing  3.426GB/4.636GBPushing  4.162GB/4.636GBPushing  4.632GB/4.636GB20240906205431: digest: sha256:0c6697484b8859ddcb6107081a209d31cfae0fa6ee2203aa6bd9edb9010ef5b8 size: 6187
Saving ECR image URI into ecr_image_fullname.txt


To verify that the image was correctly pushed to the [Elastic Container Registry](https://aws.amazon.com/ecr/), you can look at it in the AWS webapp. For example, below you can see that three different images have been pushed to ECR. You should only see one, called `tf2-object-detection`.
![ECR Example](../data/example_ecr.png)


In [7]:
# display the container name
with open (os.path.join('docker', 'ecr_image_fullname.txt'), 'r') as f:
    container = f.readlines()[0][:-1]

print(container)

038462780242.dkr.ecr.us-east-1.amazonaws.com/tf2-object-detection:20240906205431


## Pre-trained model from model zoo

As often, we are not training from scratch and we will be using a pretrained model from the TF Object Detection model zoo. You can find pretrained checkpoints [here](https://github.com/tensorflow/models/blob/master/research/object_detection/g3doc/tf2_detection_zoo.md). Because your time is limited for this project, we recommend to only experiment with the following models:
* SSD MobileNet V2 FPNLite 640x640	
* SSD ResNet50 V1 FPN 640x640 (RetinaNet50)	
* Faster R-CNN ResNet50 V1 640x640	
* EfficientDet D1 640x640	
* Faster R-CNN ResNet152 V1 640x640	

In the code below, the EfficientDet D1 model is downloaded and extracted. This code should be adjusted if you were to experiment with other architectures.

In [8]:
%%bash
mkdir /tmp/checkpoint
mkdir source_dir/checkpoint
wget -O /tmp/efficientdet.tar.gz http://download.tensorflow.org/models/object_detection/tf2/20200711/efficientdet_d1_coco17_tpu-32.tar.gz
tar -zxvf /tmp/efficientdet.tar.gz --strip-components 2 --directory source_dir/checkpoint efficientdet_d1_coco17_tpu-32/checkpoint

--2024-09-06 21:11:27--  http://download.tensorflow.org/models/object_detection/tf2/20200711/efficientdet_d1_coco17_tpu-32.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 142.251.179.207, 64.233.180.207, 142.251.16.207, ...
Connecting to download.tensorflow.org (download.tensorflow.org)|142.251.179.207|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 51839363 (49M) [application/x-tar]
Saving to: ‘/tmp/efficientdet.tar.gz’

     0K .......... .......... .......... .......... ..........  0% 9.20M 5s
    50K .......... .......... .......... .......... ..........  0% 18.3M 4s
   100K .......... .......... .......... .......... ..........  0% 17.8M 4s
   150K .......... .......... .......... .......... ..........  0% 13.3M 4s
   200K .......... .......... .......... .......... ..........  0% 18.5M 3s
   250K .......... .......... .......... .......... ..........  0% 17.6M 3s
   300K .......... .......... .......... .......... ..........  0% 14.6

  5100K .......... .......... .......... .......... .......... 10% 36.8M 2s
  5150K .......... .......... .......... .......... .......... 10% 36.0M 2s
  5200K .......... .......... .......... .......... .......... 10% 47.0M 1s
  5250K .......... .......... .......... .......... .......... 10% 36.7M 1s
  5300K .......... .......... .......... .......... .......... 10% 82.7M 1s
  5350K .......... .......... .......... .......... .......... 10% 34.8M 1s
  5400K .......... .......... .......... .......... .......... 10% 38.7M 1s
  5450K .......... .......... .......... .......... .......... 10% 48.1M 1s
  5500K .......... .......... .......... .......... .......... 10% 43.6M 1s
  5550K .......... .......... .......... .......... .......... 11% 63.1M 1s
  5600K .......... .......... .......... .......... .......... 11% 34.3M 1s
  5650K .......... .......... .......... .......... .......... 11% 38.9M 1s
  5700K .......... .......... .......... .......... .......... 11% 48.4M 1s
  5750K ....

 10500K .......... .......... .......... .......... .......... 20% 72.3M 1s
 10550K .......... .......... .......... .......... .......... 20%  321M 1s
 10600K .......... .......... .......... .......... .......... 21% 76.7M 1s
 10650K .......... .......... .......... .......... .......... 21% 66.9M 1s
 10700K .......... .......... .......... .......... .......... 21% 79.7M 1s
 10750K .......... .......... .......... .......... .......... 21% 56.6M 1s
 10800K .......... .......... .......... .......... .......... 21%  315M 1s
 10850K .......... .......... .......... .......... .......... 21%  105M 1s
 10900K .......... .......... .......... .......... .......... 21% 84.3M 1s
 10950K .......... .......... .......... .......... .......... 21% 58.6M 1s
 11000K .......... .......... .......... .......... .......... 21%  112M 1s
 11050K .......... .......... .......... .......... .......... 21%  228M 1s
 11100K .......... .......... .......... .......... .......... 22% 76.3M 1s
 11150K ....

 15900K .......... .......... .......... .......... .......... 31%  259M 1s
 15950K .......... .......... .......... .......... .......... 31%  134M 1s
 16000K .......... .......... .......... .......... .......... 31%  132M 1s
 16050K .......... .......... .......... .......... .......... 31%  115M 1s
 16100K .......... .......... .......... .......... .......... 31%  221M 1s
 16150K .......... .......... .......... .......... .......... 32%  120M 1s
 16200K .......... .......... .......... .......... .......... 32%  135M 1s
 16250K .......... .......... .......... .......... .......... 32%  149M 1s
 16300K .......... .......... .......... .......... .......... 32%  315M 1s
 16350K .......... .......... .......... .......... .......... 32% 1.97M 1s
 16400K .......... .......... .......... .......... .......... 32%  145M 1s
 16450K .......... .......... .......... .......... .......... 32%  253M 1s
 16500K .......... .......... .......... .......... .......... 32%  167M 1s
 16550K ....

 21300K .......... .......... .......... .......... .......... 42%  245M 0s
 21350K .......... .......... .......... .......... .......... 42%  324M 0s
 21400K .......... .......... .......... .......... .......... 42%  103M 0s
 21450K .......... .......... .......... .......... .......... 42%  241M 0s
 21500K .......... .......... .......... .......... .......... 42%  207M 0s
 21550K .......... .......... .......... .......... .......... 42%  209M 0s
 21600K .......... .......... .......... .......... .......... 42%  382M 0s
 21650K .......... .......... .......... .......... .......... 42%  272M 0s
 21700K .......... .......... .......... .......... .......... 42%  227M 0s
 21750K .......... .......... .......... .......... .......... 43%  320M 0s
 21800K .......... .......... .......... .......... .......... 43%  219M 0s
 21850K .......... .......... .......... .......... .......... 43%  119M 0s
 21900K .......... .......... .......... .......... .......... 43%  139M 0s
 21950K ....

...

 32100K .......... .......... .......... .......... .......... 63%  390M 0s
 32150K .......... .......... .......... .......... .......... 63%  454M 0s
 32200K .......... .......... .......... .......... .......... 63%  451M 0s
 32250K .......... .......... .......... .......... .......... 63%  451M 0s
 32300K .......... .......... .......... .......... .......... 63%  319M 0s
 32350K .......... .......... .......... .......... .......... 64%  406M 0s
 32400K .......... .......... .......... .......... .......... 64%  455M 0s
 32450K .......... .......... .......... .......... .......... 64%  434M 0s
 32500K .......... .......... .......... .......... .......... 64%  318M 0s
 32550K .......... .......... .......... .......... .......... 64%  391M 0s
 32600K .......... .......... .......... .......... .......... 64%  458M 0s
 32650K .......... .......... .......... .......... .......... 64%  452M 0s
 32700K .......... .......... .......... .......... .......... 64%  374M 0s
 32750K ....

 37500K .......... .......... .......... .......... .......... 74%  359M 0s
 37550K .......... .......... .......... .......... .......... 74%  283M 0s
 37600K .......... .......... .......... .......... .......... 74%  311M 0s
 37650K .......... .......... .......... .......... .......... 74%  330M 0s
 37700K .......... .......... .......... .......... .......... 74%  292M 0s
 37750K .......... .......... .......... .......... .......... 74%  348M 0s
 37800K .......... .......... .......... .......... .......... 74%  194M 0s
 37850K .......... .......... .......... .......... .......... 74%  257M 0s
 37900K .......... .......... .......... .......... .......... 74%  335M 0s
 37950K .......... .......... .......... .......... .......... 75%  348M 0s
 38000K .......... .......... .......... .......... .......... 75%  274M 0s
 38050K .......... .......... .......... .......... .......... 75%  289M 0s
 38100K .......... .......... .......... .......... .......... 75%  360M 0s
 38150K ....

 42900K .......... .......... .......... .......... .......... 84%  206M 0s
 42950K .......... .......... .......... .......... .......... 84%  216M 0s
 43000K .......... .......... .......... .......... .......... 85%  194M 0s
 43050K .......... .......... .......... .......... .......... 85%  297M 0s
 43100K .......... .......... .......... .......... .......... 85%  197M 0s
 43150K .......... .......... .......... .......... .......... 85%  252M 0s
 43200K .......... .......... .......... .......... .......... 85%  244M 0s
 43250K .......... .......... .......... .......... .......... 85%  201M 0s
 43300K .......... .......... .......... .......... .......... 85%  216M 0s
 43350K .......... .......... .......... .......... .......... 85%  191M 0s
 43400K .......... .......... .......... .......... .......... 85%  303M 0s
 43450K .......... .......... .......... .......... .......... 85%  227M 0s
 43500K .......... .......... .......... .......... .......... 86%  165M 0s
 43550K ....

 48300K .......... .......... .......... .......... .......... 95%  206M 0s
 48350K .......... .......... .......... .......... .......... 95%  308M 0s
 48400K .......... .......... .......... .......... .......... 95%  415M 0s
 48450K .......... .......... .......... .......... .......... 95%  409M 0s
 48500K .......... .......... .......... .......... .......... 95%  330M 0s
 48550K .......... .......... .......... .......... .......... 96%  199M 0s
 48600K .......... .......... .......... .......... .......... 96%  356M 0s
 48650K .......... .......... .......... .......... .......... 96%  379M 0s
 48700K .......... .......... .......... .......... .......... 96%  323M 0s
 48750K .......... .......... .......... .......... .......... 96%  123M 0s
 48800K .......... .......... .......... .......... .......... 96%  308M 0s
 48850K .......... .......... .......... .......... .......... 96%  175M 0s
 48900K .......... .......... .......... .......... .......... 96%  231M 0s
 48950K ....

efficientdet_d1_coco17_tpu-32/checkpoint/ckpt-0.data-00000-of-00001
efficientdet_d1_coco17_tpu-32/checkpoint/checkpoint
efficientdet_d1_coco17_tpu-32/checkpoint/ckpt-0.index


In [ ]:
# Sid's checks 

In [19]:
%%bash

ls /tmp/

checkpoint
efficientdet.tar.gz
hsperfdata_role-agent
jetty-localhost-9081-role-proxy-agent_war-_-any-5548744550284064542
systemd-private-f44b2f4fd0364b3b835c21bd348d5dc0-chronyd.service-5Yp43k


## Edit pipeline.config file

The [`pipeline.config`](source_dir/pipeline.config) in the `source_dir` folder should be updated when you experiment with different models. The different config files are available [here](https://github.com/tensorflow/models/tree/master/research/object_detection/configs/tf2).

>Note: The provided `pipeline.config` file works well with the `EfficientDet` model. You would need to modify it when working with other models.

## Launch Training Job

Now that we have a dataset, a docker image and some pretrained model weights, we can launch the training job. To do so, we create a [Sagemaker Framework](https://sagemaker.readthedocs.io/en/stable/frameworks/index.html), where we indicate the container name, name of the config file, number of training steps etc.

The `run_training.sh` script does the following:
* train the model for `num_train_steps` 
* evaluate over the val dataset
* export the model

Different metrics will be displayed during the evaluation phase, including the mean average precision. These metrics can be used to quantify your model performances and compare over the different iterations.

You can also monitor the training progress by navigating to **Training -> Training Jobs** from the Amazon Sagemaker dashboard in the Web UI.

You should be able to see your model training in the AWS webapp as shown below:
![ECR Example](../data/example_trainings.png)


## Improve on the initial model

Most likely, this initial experiment did not yield optimal results. However, you can make multiple changes to the `pipeline.config` file to improve this model. One obvious change consists in improving the data augmentation strategy. The [`preprocessor.proto`](https://github.com/tensorflow/models/blob/master/research/object_detection/protos/preprocessor.proto) file contains the different data augmentation method available in the Tf Object Detection API. Justify your choices of augmentations in the write-up.

Keep in mind that the following are also available:
* experiment with the optimizer: type of optimizer, learning rate, scheduler etc
* experiment with the architecture. The Tf Object Detection API model zoo offers many architectures. Keep in mind that the pipeline.config file is unique for each architecture and you will have to edit it.
* visualize results on the test frames using the `2_deploy_model` notebook available in this repository.

In the cell below, write down all the different approaches you have experimented with, why you have chosen them and what you would have done if you had more time and resources. Justify your choices using the tensorboard visualizations (take screenshots and insert them in your write-up), the metrics on the evaluation set and the generated animation you have created with [this tool](../2_run_inference/2_deploy_model.ipynb).

In [ ]:
# your write-up goes here.

# zz_SID : Using a different Pre-trained model from model zoo
As often, we are not training from scratch and we will be using a pretrained model from the TF Object Detection model zoo. You can find pretrained checkpoints here. Because your time is limited for this project, we recommend to only experiment with the following models:

# Choice 1 : SSD MobileNet V2 FPNLite 640x640


In [20]:
# The train and val paths below are public S3 buckets created by Udacity for this project
inputs = {'train': 's3://cd2688-object-detection-tf2/train/', 
          'val': 's3://cd2688-object-detection-tf2/val/'} 

# Insert path of a folder in your personal S3 bucket to store tensorboard logs.
tensorboard_s3_prefix = 's3://object.detection.project/logs_SSDMobileNetV2/'

In [21]:
# display the container name, verifying again for the new model
with open (os.path.join('docker', 'ecr_image_fullname.txt'), 'r') as f:
    container = f.readlines()[0][:-1]

print(container)

038462780242.dkr.ecr.us-east-1.amazonaws.com/tf2-object-detection:20240906205431


In [22]:
"""
Steps done before loading a new model:
    1. changed s3 log path
    2. duplicated working efficientDet model's notebook progress to continue implementing newer models
    3. remaned checkpoint file
"""

'\nSteps done before loading a new model:\n'

In [32]:
%%bash

#rm -r /tmp/checkpoint
#ls /tmp
ls source_dir


checkpoint_EfficientDet
exporter_main_v2.py
model_main_tf2.py
pipeline.config
run_training.sh


# Extacting SSD MobileNet V2 FPNLite 640x640

In [33]:
%%bash
mkdir /tmp/checkpoint
mkdir source_dir/checkpoint
wget -O /tmp/ssd_mobilenet_v2.tar.gz http://download.tensorflow.org/models/object_detection/tf2/20200711/ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8.tar.gz
#tar -zxvf /tmp/efficientdet.tar.gz --strip-components 2 --directory source_dir/checkpoint efficientdet_d1_coco17_tpu-32/checkpoint

--2024-09-06 23:39:23--  http://download.tensorflow.org/models/object_detection/tf2/20200711/ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 142.251.111.207, 142.251.179.207, 64.233.180.207, ...
Connecting to download.tensorflow.org (download.tensorflow.org)|142.251.111.207|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 20518283 (20M) [application/x-tar]
Saving to: ‘/tmp/ssd_mobilenet_v2.tar.gz’

     0K .......... .......... .......... .......... ..........  0% 13.0M 1s
    50K .......... .......... .......... .......... ..........  0% 25.8M 1s
   100K .......... .......... .......... .......... ..........  0% 20.1M 1s
   150K .......... .......... .......... .......... ..........  0% 25.1M 1s
   200K .......... .......... .......... .......... ..........  1% 23.4M 1s
   250K .......... .......... .......... .......... ..........  1% 60.1M 1s
   300K .......... .......... .......... .........

  5100K .......... .......... .......... .......... .......... 25%  206M 0s
  5150K .......... .......... .......... .......... .......... 25% 66.8M 0s
  5200K .......... .......... .......... .......... .......... 26% 73.4M 0s
  5250K .......... .......... .......... .......... .......... 26% 71.4M 0s
  5300K .......... .......... .......... .......... .......... 26% 87.7M 0s
  5350K .......... .......... .......... .......... .......... 26%  140M 0s
  5400K .......... .......... .......... .......... .......... 27% 88.4M 0s
  5450K .......... .......... .......... .......... .......... 27% 72.0M 0s
  5500K .......... .......... .......... .......... .......... 27% 76.8M 0s
  5550K .......... .......... .......... .......... .......... 27%  124M 0s
  5600K .......... .......... .......... .......... .......... 28%  165M 0s
  5650K .......... .......... .......... .......... .......... 28% 69.2M 0s
  5700K .......... .......... .......... .......... .......... 28% 76.5M 0s
  5750K ....

 10500K .......... .......... .......... .......... .......... 52% 68.0M 0s
 10550K .......... .......... .......... .......... .......... 52%  131M 0s
 10600K .......... .......... .......... .......... .......... 53%  179M 0s
 10650K .......... .......... .......... .......... .......... 53%  234M 0s
 10700K .......... .......... .......... .......... .......... 53%  199M 0s
 10750K .......... .......... .......... .......... .......... 53%  104M 0s
 10800K .......... .......... .......... .......... .......... 54% 54.0M 0s
 10850K .......... .......... .......... .......... .......... 54% 78.5M 0s
 10900K .......... .......... .......... .......... .......... 54% 93.6M 0s
 10950K .......... .......... .......... .......... .......... 54%  139M 0s
 11000K .......... .......... .......... .......... .......... 55%  156M 0s
 11050K .......... .......... .......... .......... .......... 55% 99.4M 0s
 11100K .......... .......... .......... .......... .......... 55%  150M 0s
 11150K ....

 15900K .......... .......... .......... .......... .......... 79%  172M 0s
 15950K .......... .......... .......... .......... .......... 79%  153M 0s
 16000K .......... .......... .......... .......... .......... 80%  184M 0s
 16050K .......... .......... .......... .......... .......... 80%  307M 0s
 16100K .......... .......... .......... .......... .......... 80%  165M 0s
 16150K .......... .......... .......... .......... .......... 80%  165M 0s
 16200K .......... .......... .......... .......... .......... 81%  177M 0s
 16250K .......... .......... .......... .......... .......... 81%  163M 0s
 16300K .......... .......... .......... .......... .......... 81%  243M 0s
 16350K .......... .......... .......... .......... .......... 81%  391K 0s
 16400K .......... .......... .......... .......... .......... 82%  136M 0s
 16450K .......... .......... .......... .......... .......... 82%  246M 0s
 16500K .......... .......... .......... .......... .......... 82%  166M 0s
 16550K ....

In [39]:
%%bash

#rm -r /tmp/checkpoint
#ls /tmp
#ls source_dir
tar -tzf /tmp/ssd_mobilenet_v2.tar.gz

ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/checkpoint/
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/checkpoint/ckpt-0.data-00000-of-00001
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/checkpoint/checkpoint
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/checkpoint/ckpt-0.index
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/pipeline.config
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/saved_model/
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/saved_model/saved_model.pb
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/saved_model/variables/
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/saved_model/variables/variables.data-00000-of-00001
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/saved_model/variables/variables.index


In [45]:
%%bash

ls source_dir

checkpoint
checkpoint_EfficientDet
exporter_main_v2.py
model_main_tf2.py
pipeline.config
run_training.sh


In [46]:
%%bash

tar -zxvf /tmp/ssd_mobilenet_v2.tar.gz --strip-components 2 --directory source_dir/checkpoint ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/checkpoint

ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/checkpoint/ckpt-0.data-00000-of-00001
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/checkpoint/checkpoint
ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8/checkpoint/ckpt-0.index


In [48]:
# extracted the checpoint files successfully, the EfficientDet was 33MB, while ssd_mobile is 10MB. 
# Confirmed that the checkpoint files are properly extracted!

# Editing pipeline.config file for SSD MobileNet V2 FPNLite 640x640

In [51]:
# using ssd_mobilenet_v2_fpnlite_640x640_coco17_tpu-8.config as Reference
# EfficientDet pipeline.config file duplicated and renamed as pipeline_EfficientDet.config 
# editing pipeline.config file with the ssd_mobile_net_v2 specs


In [52]:
# compared the efficient net config with tensorflow model net has following differences:
    # in train_config - efficientNet uses 'use_bfloat16: true' removed for now
    # matched num_steps to 50000 in mobilenet from 300000 in efficientnet
    # in data augmentation options random_crop_image in mobilenet v/s random_crop_and_pad_to_square in efficientnet /
    #        / used random_crop_image for now
    # copied optimizer from mobilenet (differences in number of steps 50000 vs 3000000, warmup_learning_rate and warmup_steps )
    
# copied model as is from mobilenet
    
    

# Launch Training Job for SSD MobileNet V2 FPNLite 640x640

In [ ]:
# training the pretrained checkpoint for 50000 num_steps

In [55]:
tensorboard_output_config = sagemaker.debugger.TensorBoardOutputConfig(
    s3_output_path=tensorboard_s3_prefix,
    container_local_output_path='/opt/training/'
)

estimator = CustomFramework(
    role=role,
    image_uri=container,
    entry_point='run_training.sh',
    source_dir='source_dir/',
    hyperparameters={
        "model_dir": "/opt/training",        
        "pipeline_config_path": "pipeline.config",
        "num_train_steps": "2000",    
        "sample_1_of_n_eval_examples": "1"
    },
    instance_count=1,
    instance_type='ml.g5.xlarge',
    tensorboard_output_config=tensorboard_output_config,
    disable_profiler=True,
    base_job_name='tf2-object-detection'
)

estimator.fit(inputs)

INFO:sagemaker:Creating training-job with name: tf2-object-detection-2024-09-07-03-49-50-202


2024-09-07 03:49:54 Starting - Starting the training job...
2024-09-07 03:50:11 Starting - Preparing the instances for training...
2024-09-07 03:50:45 Downloading - Downloading input data...
2024-09-07 03:51:05 Downloading - Downloading the training image............
2024-09-07 03:53:22 Training - Training image download completed. Training in progress...2024-09-07 03:53:35,882 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 03:53:35,917 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 03:53:35,951 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 03:53:35,965 sagemaker-training-toolkit INFO     Invoking user script
Training Env:
{
    "additional_framework_parameters": {},
    "channel_input_dirs": {
        "train": "/opt/ml/input/data/train",
        "val": "/opt/ml/input/data/val"
    },
    "current_host": "algo-1",
    "current_i

Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
W0907 03:53:48.841374 140473514465088 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: sparse_to_dense (from tensorflow.python.ops.sparse_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
Instructions for updating:
`seed2` arg is deprecated.Use sample_distorted_bounding_box_v2 instead.
W0907 03:53:51.630250 140473514465088 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: sample_distorted_bounding_box (from tensorflow.python.ops.image_ops_impl) is deprecated and will be removed in a future version.
Instructions for updating:
`seed2` arg is deprecated.Use sample_distorted_bounding_box_v2 instead.
Instructions for updating:
Use `tf.cast` instead.
W0907 03:53:53.026086 140473

INFO:tensorflow:Step 300 per-step time 0.223s
I0907 03:55:53.377346 140473514465088 model_lib_v2.py:705] Step 300 per-step time 0.223s
INFO:tensorflow:{'Loss/classification_loss': 0.22756398,
 'Loss/localization_loss': 0.29801497,
 'Loss/regularization_loss': 0.15136707,
 'Loss/total_loss': 0.67694604,
 'learning_rate': 0.0426662}
I0907 03:55:53.377588 140473514465088 model_lib_v2.py:708] {'Loss/classification_loss': 0.22756398,
 'Loss/localization_loss': 0.29801497,
 'Loss/regularization_loss': 0.15136707,
 'Loss/total_loss': 0.67694604,
 'learning_rate': 0.0426662}
INFO:tensorflow:Step 400 per-step time 0.223s
I0907 03:56:15.670792 140473514465088 model_lib_v2.py:705] Step 400 per-step time 0.223s
INFO:tensorflow:{'Loss/classification_loss': 0.23254122,
 'Loss/localization_loss': 0.33164695,
 'Loss/regularization_loss': 0.15132254,
 'Loss/total_loss': 0.7155107,
 'learning_rate': 0.047999598}
I0907 03:56:15.671067 140473514465088 model_lib_v2.py:708] {'Loss/classification_loss': 0.23

INFO:tensorflow:Step 1700 per-step time 0.223s
I0907 04:01:06.323195 140473514465088 model_lib_v2.py:705] Step 1700 per-step time 0.223s
INFO:tensorflow:{'Loss/classification_loss': 0.18312247,
 'Loss/localization_loss': 0.24397342,
 'Loss/regularization_loss': 0.14960267,
 'Loss/total_loss': 0.57669854,
 'learning_rate': 0.07995972}
I0907 04:01:06.323440 140473514465088 model_lib_v2.py:708] {'Loss/classification_loss': 0.18312247,
 'Loss/localization_loss': 0.24397342,
 'Loss/regularization_loss': 0.14960267,
 'Loss/total_loss': 0.57669854,
 'learning_rate': 0.07995972}
INFO:tensorflow:Step 1800 per-step time 0.223s
I0907 04:01:28.591977 140473514465088 model_lib_v2.py:705] Step 1800 per-step time 0.223s
INFO:tensorflow:{'Loss/classification_loss': 0.18745562,
 'Loss/localization_loss': 0.2944703,
 'Loss/regularization_loss': 0.14932612,
 'Loss/total_loss': 0.63125205,
 'learning_rate': 0.0799474}
I0907 04:01:28.592233 140473514465088 model_lib_v2.py:708] {'Loss/classification_loss': 

I0907 04:02:43.089893 140411732674368 api.py:460] feature_map_spatial_dims: [(80, 80), (40, 40), (20, 20), (10, 10), (5, 5)]
Instructions for updating:
Use `tf.cast` instead.
W0907 04:02:46.934302 140411732674368 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: to_int64 (from tensorflow.python.ops.math_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.cast` instead.
INFO:tensorflow:Finished eval step 0
I0907 04:02:47.029660 140411732674368 model_lib_v2.py:966] Finished eval step 0
Instructions for updating:
tf.py_func is deprecated in TF V2. Instead, there are two
    options available in V2.
    - tf.py_function takes a python function which manipulates tf eager
    tensors instead of numpy arrays. It's easy to convert a tf eager tensor to
    an ndarray (just call tensor.numpy()) but having access to eager tensors
    means `tf.py_function`s can use accelerators such as GPUs as well a

I0907 04:07:52.441350 140531446409024 api.py:460] feature_map_spatial_dims: [(80, 80), (40, 40), (20, 20), (10, 10), (5, 5)]
I0907 04:07:54.771868 140531446409024 signature_serialization.py:148] Function `call_func` contains input name(s) resource with unsupported characters which will be renamed to weightsharedconvolutionalboxpredictor_predictiontower_conv2d_3_batchnorm_feature_4_fusedbatchnormv3_readvariableop_1_resource in the SavedModel.
I0907 04:07:55.822627 140531446409024 api.py:460] feature_map_spatial_dims: [(80, 80), (40, 40), (20, 20), (10, 10), (5, 5)]
W0907 04:07:57.660760 140531446409024 save_impl.py:66] Skipping full serialization of Keras layer <object_detection.meta_architectures.ssd_meta_arch.SSDMetaArch object at 0x7fcefc1530d0>, because it is not built.
W0907 04:07:58.074788 140531446409024 save_impl.py:66] Skipping full serialization of Keras layer <keras.src.layers.convolutional.separable_conv2d.SeparableConv2D object at 0x7fceb3dc00a0>, because it is not built.
W

I0907 04:08:07.596927 140531446409024 save.py:274] Found untraced functions such as WeightSharedConvolutionalBoxPredictor_layer_call_fn, WeightSharedConvolutionalBoxPredictor_layer_call_and_return_conditional_losses, WeightSharedConvolutionalBoxHead_layer_call_fn, WeightSharedConvolutionalBoxHead_layer_call_and_return_conditional_losses, WeightSharedConvolutionalClassHead_layer_call_fn while saving (showing 5 of 173). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: /tmp/exported/saved_model/assets
I0907 04:08:12.881333 140531446409024 builder_impl.py:804] Assets written to: /tmp/exported/saved_model/assets
I0907 04:08:13.232013 140531446409024 fingerprinting_utils.py:48] Writing fingerprint to /tmp/exported/saved_model/fingerprint.pb
INFO:tensorflow:Writing pipeline config file to /tmp/exported/pipeline.config
I0907 04:08:13.645214 140531446409024 config_util.py:253] Writing pipeline config file to /tmp/exported/pipeline.config
2024-09-07

In [ ]:
# training the pretrained checkpoint for 300000 num_steps

In [57]:
tensorboard_output_config = sagemaker.debugger.TensorBoardOutputConfig(
    s3_output_path=tensorboard_s3_prefix,
    container_local_output_path='/opt/training/'
)

estimator = CustomFramework(
    role=role,
    image_uri=container,
    entry_point='run_training.sh',
    source_dir='source_dir/',
    hyperparameters={
        "model_dir": "/opt/training",        
        "pipeline_config_path": "pipeline.config",
        "num_train_steps": "2000",    
        "sample_1_of_n_eval_examples": "1"
    },
    instance_count=1,
    instance_type='ml.g5.xlarge',
    tensorboard_output_config=tensorboard_output_config,
    disable_profiler=True,
    base_job_name='tf2-object-detection'
)

estimator.fit(inputs)

INFO:sagemaker:Creating training-job with name: tf2-object-detection-2024-09-07-04-28-06-606


2024-09-07 04:28:10 Starting - Starting the training job...
2024-09-07 04:28:24 Starting - Preparing the instances for training...
2024-09-07 04:29:04 Downloading - Downloading the training image...............
2024-09-07 04:31:31 Training - Training image download completed. Training in progress..2024-09-07 04:31:42,586 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 04:31:42,621 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 04:31:42,655 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 04:31:42,670 sagemaker-training-toolkit INFO     Invoking user script
Training Env:
{
    "additional_framework_parameters": {},
    "channel_input_dirs": {
        "train": "/opt/ml/input/data/train",
        "val": "/opt/ml/input/data/val"
    },
    "current_host": "algo-1",
    "current_instance_group": "homogeneousCluster",
    "current_instanc

Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
W0907 04:31:55.579324 140236452955968 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: sparse_to_dense (from tensorflow.python.ops.sparse_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
Instructions for updating:
`seed2` arg is deprecated.Use sample_distorted_bounding_box_v2 instead.
W0907 04:31:58.339059 140236452955968 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: sample_distorted_bounding_box (from tensorflow.python.ops.image_ops_impl) is deprecated and will be removed in a future version.
Instructions for updating:
`seed2` arg is deprecated.Use sample_distorted_bounding_box_v2 instead.
Instructions for updating:
Use `tf.cast` instead.
W0907 04:31:59.727734 140236

INFO:tensorflow:Step 300 per-step time 0.221s
I0907 04:33:59.451000 140236452955968 model_lib_v2.py:705] Step 300 per-step time 0.221s
INFO:tensorflow:{'Loss/classification_loss': 0.2158271,
 'Loss/localization_loss': 0.3136094,
 'Loss/regularization_loss': 0.15133515,
 'Loss/total_loss': 0.6807716,
 'learning_rate': 0.0426662}
I0907 04:33:59.451243 140236452955968 model_lib_v2.py:708] {'Loss/classification_loss': 0.2158271,
 'Loss/localization_loss': 0.3136094,
 'Loss/regularization_loss': 0.15133515,
 'Loss/total_loss': 0.6807716,
 'learning_rate': 0.0426662}
INFO:tensorflow:Step 400 per-step time 0.221s
I0907 04:34:21.578131 140236452955968 model_lib_v2.py:705] Step 400 per-step time 0.221s
INFO:tensorflow:{'Loss/classification_loss': 0.23366804,
 'Loss/localization_loss': 0.30379066,
 'Loss/regularization_loss': 0.15128864,
 'Loss/total_loss': 0.68874735,
 'learning_rate': 0.047999598}
I0907 04:34:21.578402 140236452955968 model_lib_v2.py:708] {'Loss/classification_loss': 0.2336680

INFO:tensorflow:Step 1700 per-step time 0.221s
I0907 04:39:10.212282 140236452955968 model_lib_v2.py:705] Step 1700 per-step time 0.221s
INFO:tensorflow:{'Loss/classification_loss': 0.18640408,
 'Loss/localization_loss': 0.26989505,
 'Loss/regularization_loss': 0.14965895,
 'Loss/total_loss': 0.6059581,
 'learning_rate': 0.07999892}
I0907 04:39:10.212550 140236452955968 model_lib_v2.py:708] {'Loss/classification_loss': 0.18640408,
 'Loss/localization_loss': 0.26989505,
 'Loss/regularization_loss': 0.14965895,
 'Loss/total_loss': 0.6059581,
 'learning_rate': 0.07999892}
INFO:tensorflow:Step 1800 per-step time 0.221s
I0907 04:39:32.339998 140236452955968 model_lib_v2.py:705] Step 1800 per-step time 0.221s
INFO:tensorflow:{'Loss/classification_loss': 0.21659994,
 'Loss/localization_loss': 0.3545006,
 'Loss/regularization_loss': 0.14933696,
 'Loss/total_loss': 0.7204375,
 'learning_rate': 0.07999859}
I0907 04:39:32.340238 140236452955968 model_lib_v2.py:708] {'Loss/classification_loss': 0.

I0907 04:40:46.495495 140087344904000 api.py:460] feature_map_spatial_dims: [(80, 80), (40, 40), (20, 20), (10, 10), (5, 5)]
Instructions for updating:
Use `tf.cast` instead.
W0907 04:40:50.163186 140087344904000 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: to_int64 (from tensorflow.python.ops.math_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.cast` instead.
INFO:tensorflow:Finished eval step 0
I0907 04:40:50.258529 140087344904000 model_lib_v2.py:966] Finished eval step 0
Instructions for updating:
tf.py_func is deprecated in TF V2. Instead, there are two
    options available in V2.
    - tf.py_function takes a python function which manipulates tf eager
    tensors instead of numpy arrays. It's easy to convert a tf eager tensor to
    an ndarray (just call tensor.numpy()) but having access to eager tensors
    means `tf.py_function`s can use accelerators such as GPUs as well a

I0907 04:45:55.737105 139729359824704 api.py:460] feature_map_spatial_dims: [(80, 80), (40, 40), (20, 20), (10, 10), (5, 5)]
I0907 04:45:58.052803 139729359824704 signature_serialization.py:148] Function `call_func` contains input name(s) resource with unsupported characters which will be renamed to weightsharedconvolutionalboxpredictor_predictiontower_conv2d_3_batchnorm_feature_4_fusedbatchnormv3_readvariableop_1_resource in the SavedModel.
I0907 04:45:59.092366 139729359824704 api.py:460] feature_map_spatial_dims: [(80, 80), (40, 40), (20, 20), (10, 10), (5, 5)]
W0907 04:46:00.932082 139729359824704 save_impl.py:66] Skipping full serialization of Keras layer <object_detection.meta_architectures.ssd_meta_arch.SSDMetaArch object at 0x7f1490091c40>, because it is not built.
W0907 04:46:01.343270 139729359824704 save_impl.py:66] Skipping full serialization of Keras layer <keras.src.layers.convolutional.separable_conv2d.SeparableConv2D object at 0x7f13f3c3afd0>, because it is not built.
W


2024-09-07 04:46:24 Uploading - Uploading generated training modelI0907 04:46:10.795715 139729359824704 save.py:274] Found untraced functions such as WeightSharedConvolutionalBoxPredictor_layer_call_fn, WeightSharedConvolutionalBoxPredictor_layer_call_and_return_conditional_losses, WeightSharedConvolutionalBoxHead_layer_call_fn, WeightSharedConvolutionalBoxHead_layer_call_and_return_conditional_losses, WeightSharedConvolutionalClassHead_layer_call_fn while saving (showing 5 of 173). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: /tmp/exported/saved_model/assets
I0907 04:46:16.052671 139729359824704 builder_impl.py:804] Assets written to: /tmp/exported/saved_model/assets
I0907 04:46:16.403460 139729359824704 fingerprinting_utils.py:48] Writing fingerprint to /tmp/exported/saved_model/fingerprint.pb
INFO:tensorflow:Writing pipeline config file to /tmp/exported/pipeline.config
I0907 04:46:16.823820 139729359824704 config_util.py:253] Writi

# zz_SID : Using a different Pre-trained model from model zoo
As often, we are not training from scratch and we will be using a pretrained model from the TF Object Detection model zoo. You can find pretrained checkpoints here. Because your time is limited for this project, we recommend to only experiment with the following models:

# Choice 2 : Faster R-CNN ResNet50 V1 640x640

In [59]:
# The train and val paths below are public S3 buckets created by Udacity for this project
inputs = {'train': 's3://cd2688-object-detection-tf2/train/', 
          'val': 's3://cd2688-object-detection-tf2/val/'} 

# Insert path of a folder in your personal S3 bucket to store tensorboard logs.
tensorboard_s3_prefix = 's3://object.detection.project/logs_FasterRCNNResNet50V1/'

In [60]:
# display the container name, verifying again for the new model
with open (os.path.join('docker', 'ecr_image_fullname.txt'), 'r') as f:
    container = f.readlines()[0][:-1]

print(container)

038462780242.dkr.ecr.us-east-1.amazonaws.com/tf2-object-detection:20240906205431


In [61]:
%%bash

#rm -r /tmp/checkpoint
ls /tmp
#ls source_dir


checkpoint
efficientdet.tar.gz
hsperfdata_role-agent
jetty-localhost-9081-role-proxy-agent_war-_-any-5548744550284064542
ssd_mobilenet_v2.tar.gz
systemd-private-f44b2f4fd0364b3b835c21bd348d5dc0-chronyd.service-5Yp43k


In [62]:
%%bash
mkdir /tmp/checkpoint
mkdir source_dir/checkpoint
wget -O /tmp/fasterRcnnResnet50v1.tar.gz http://download.tensorflow.org/models/object_detection/tf2/20200711/faster_rcnn_resnet50_v1_640x640_coco17_tpu-8.tar.gz
#tar -zxvf /tmp/efficientdet.tar.gz --strip-components 2 --directory source_dir/checkpoint efficientdet_d1_coco17_tpu-32/checkpoint

mkdir: cannot create directory ‘/tmp/checkpoint’: File exists
--2024-09-07 05:06:24--  http://download.tensorflow.org/models/object_detection/tf2/20200711/faster_rcnn_resnet50_v1_640x640_coco17_tpu-8.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 172.253.63.207, 142.250.31.207, 142.251.111.207, ...
Connecting to download.tensorflow.org (download.tensorflow.org)|172.253.63.207|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 211996178 (202M) [application/x-tar]
Saving to: ‘/tmp/fasterRcnnResnet50v1.tar.gz’

     0K .......... .......... .......... .......... ..........  0% 12.4M 16s
    50K .......... .......... .......... .......... ..........  0% 24.0M 12s
   100K .......... .......... .......... .......... ..........  0% 24.6M 11s
   150K .......... .......... .......... .......... ..........  0% 24.7M 10s
   200K .......... .......... .......... .......... ..........  0% 24.0M 10s
   250K .......... .......... .......... .......... ....

  5050K .......... .......... .......... .......... ..........  2%  249M 4s
  5100K .......... .......... .......... .......... ..........  2%  151M 4s
  5150K .......... .......... .......... .......... ..........  2%  179M 4s
  5200K .......... .......... .......... .......... ..........  2%  306M 4s
  5250K .......... .......... .......... .......... ..........  2%  322M 4s
  5300K .......... .......... .......... .......... ..........  2%  231M 4s
  5350K .......... .......... .......... .......... ..........  2%  277M 4s
  5400K .......... .......... .......... .......... ..........  2%  220M 4s
  5450K .......... .......... .......... .......... ..........  2%  125M 4s
  5500K .......... .......... .......... .......... ..........  2% 40.8M 4s
  5550K .......... .......... .......... .......... ..........  2%  106M 4s
  5600K .......... .......... .......... .......... ..........  2%  169M 4s
  5650K .......... .......... .......... .......... ..........  2%  203M 4s
  5700K ....

 10450K .......... .......... .......... .......... ..........  5%  241M 3s
 10500K .......... .......... .......... .......... ..........  5%  204M 3s
 10550K .......... .......... .......... .......... ..........  5%  278M 3s
 10600K .......... .......... .......... .......... ..........  5%  213M 2s
 10650K .......... .......... .......... .......... ..........  5%  162M 2s
 10700K .......... .......... .......... .......... ..........  5%  248M 2s
 10750K .......... .......... .......... .......... ..........  5%  283M 2s
 10800K .......... .......... .......... .......... ..........  5%  301M 2s
 10850K .......... .......... .......... .......... ..........  5%  301M 2s
 10900K .......... .......... .......... .......... ..........  5%  247M 2s
 10950K .......... .......... .......... .......... ..........  5%  204M 2s
 11000K .......... .......... .......... .......... ..........  5%  332M 2s
 11050K .......... .......... .......... .......... ..........  5%  280M 2s
 11100K ....

 15850K .......... .......... .......... .......... ..........  7%  290M 2s
 15900K .......... .......... .......... .......... ..........  7%  274M 2s
 15950K .......... .......... .......... .......... ..........  7%  288M 2s
 16000K .......... .......... .......... .......... ..........  7%  316M 2s
 16050K .......... .......... .......... .......... ..........  7%  316M 2s
 16100K .......... .......... .......... .......... ..........  7%  307M 2s
 16150K .......... .......... .......... .......... ..........  7%  297M 2s
 16200K .......... .......... .......... .......... ..........  7%  250M 2s
 16250K .......... .......... .......... .......... ..........  7%  347M 2s
 16300K .......... .......... .......... .......... ..........  7%  237M 2s
 16350K .......... .......... .......... .......... ..........  7%  287M 2s
 16400K .......... .......... .......... .......... ..........  7%  352M 2s
 16450K .......... .......... .......... .......... ..........  7%  314M 2s
 16500K ....

 21250K .......... .......... .......... .......... .......... 10%  217M 2s
 21300K .......... .......... .......... .......... .......... 10%  259M 2s
 21350K .......... .......... .......... .......... .......... 10%  187M 2s
 21400K .......... .......... .......... .......... .......... 10%  111M 2s
 21450K .......... .......... .......... .......... .......... 10%  336M 2s
 21500K .......... .......... .......... .......... .......... 10%  253M 2s
 21550K .......... .......... .......... .......... .......... 10%  214M 2s
 21600K .......... .......... .......... .......... .......... 10%  318M 2s
 21650K .......... .......... .......... .......... .......... 10%  324M 2s
 21700K .......... .......... .......... .......... .......... 10%  177M 2s
 21750K .......... .......... .......... .......... .......... 10%  132M 2s
 21800K .......... .......... .......... .......... .......... 10%  305M 2s
 21850K .......... .......... .......... .......... .......... 10%  214M 2s
 21900K ....

...

123850K .......... .......... .......... .......... .......... 59%  224M 1s
123900K .......... .......... .......... .......... .......... 59%  208M 1s
123950K .......... .......... .......... .......... .......... 59%  324M 1s
124000K .......... .......... .......... .......... .......... 59%  111M 1s
124050K .......... .......... .......... .......... .......... 59%  267M 1s
124100K .......... .......... .......... .......... .......... 59%  302M 1s
124150K .......... .......... .......... .......... .......... 59%  282M 1s
124200K .......... .......... .......... .......... .......... 60%  202M 1s
124250K .......... .......... .......... .......... .......... 60%  167M 1s
124300K .......... .......... .......... .......... .......... 60%  269M 1s
124350K .......... .......... .......... .......... .......... 60%  211M 1s
124400K .......... .......... .......... .......... .......... 60%  216M 1s
124450K .......... .......... .......... .......... .......... 60%  314M 1s
124500K ....

129250K .......... .......... .......... .......... .......... 62%  320M 1s
129300K .......... .......... .......... .......... .......... 62%  299M 1s
129350K .......... .......... .......... .......... .......... 62%  323M 1s
129400K .......... .......... .......... .......... .......... 62%  238M 1s
129450K .......... .......... .......... .......... .......... 62%  289M 1s
129500K .......... .......... .......... .......... .......... 62%  321M 1s
129550K .......... .......... .......... .......... .......... 62%  293M 1s
129600K .......... .......... .......... .......... .......... 62%  273M 1s
129650K .......... .......... .......... .......... .......... 62%  255M 1s
129700K .......... .......... .......... .......... .......... 62%  314M 1s
129750K .......... .......... .......... .......... .......... 62%  290M 1s
129800K .......... .......... .......... .......... .......... 62%  278M 1s
129850K .......... .......... .......... .......... .......... 62%  321M 1s
129900K ....

134650K .......... .......... .......... .......... .......... 65%  163M 1s
134700K .......... .......... .......... .......... .......... 65%  133M 1s
134750K .......... .......... .......... .......... .......... 65%  156M 1s
134800K .......... .......... .......... .......... .......... 65%  136M 1s
134850K .......... .......... .......... .......... .......... 65%  166M 1s
134900K .......... .......... .......... .......... .......... 65%  172M 1s
134950K .......... .......... .......... .......... .......... 65%  113M 1s
135000K .......... .......... .......... .......... .......... 65%  209M 1s
135050K .......... .......... .......... .......... .......... 65%  142M 1s
135100K .......... .......... .......... .......... .......... 65%  271M 1s
135150K .......... .......... .......... .......... .......... 65%  210M 1s
135200K .......... .......... .......... .......... .......... 65%  175M 1s
135250K .......... .......... .......... .......... .......... 65%  112M 1s
135300K ....

140050K .......... .......... .......... .......... .......... 67%  378M 1s
140100K .......... .......... .......... .......... .......... 67%  388M 1s
140150K .......... .......... .......... .......... .......... 67%  333M 1s
140200K .......... .......... .......... .......... .......... 67% 74.4M 1s
140250K .......... .......... .......... .......... .......... 67%  266M 1s
140300K .......... .......... .......... .......... .......... 67%  347M 1s
140350K .......... .......... .......... .......... .......... 67%  424M 1s
140400K .......... .......... .......... .......... .......... 67%  100M 1s
140450K .......... .......... .......... .......... .......... 67%  185M 1s
140500K .......... .......... .......... .......... .......... 67% 44.2M 1s
140550K .......... .......... .......... .......... .......... 67% 73.3M 1s
140600K .......... .......... .......... .......... .......... 67%  182M 1s
140650K .......... .......... .......... .......... .......... 67%  259M 1s
140700K ....

145450K .......... .......... .......... .......... .......... 70%  201M 1s
145500K .......... .......... .......... .......... .......... 70%  347M 1s
145550K .......... .......... .......... .......... .......... 70%  300M 1s
145600K .......... .......... .......... .......... .......... 70%  285M 1s
145650K .......... .......... .......... .......... .......... 70% 71.0M 1s
145700K .......... .......... .......... .......... .......... 70%  309M 1s
145750K .......... .......... .......... .......... .......... 70%  293M 1s
145800K .......... .......... .......... .......... .......... 70%  334M 1s
145850K .......... .......... .......... .......... .......... 70%  342M 1s
145900K .......... .......... .......... .......... .......... 70%  313M 1s
145950K .......... .......... .......... .......... .......... 70%  300M 1s
146000K .......... .......... .......... .......... .......... 70%  269M 1s
146050K .......... .......... .......... .......... .......... 70%  168M 1s
146100K ....

In [63]:
%%bash

#rm -r /tmp/checkpoint
#ls /tmp
#ls source_dir
tar -tzf /tmp/fasterRcnnResnet50v1.tar.gz

faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/checkpoint/
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/checkpoint/ckpt-0.data-00000-of-00001
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/checkpoint/checkpoint
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/checkpoint/ckpt-0.index
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/pipeline.config
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/saved_model/
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/saved_model/saved_model.pb
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/saved_model/variables/
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/saved_model/variables/variables.data-00000-of-00001
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/saved_model/variables/variables.index


In [64]:
%%bash
#mkdir /tmp/checkpoint
#mkdir source_dir/checkpoint
#wget -O /tmp/fasterRcnnResnet50v1.tar.gz http://download.tensorflow.org/models/object_detection/tf2/20200711/faster_rcnn_resnet50_v1_640x640_coco17_tpu-8.tar.gz
tar -zxvf /tmp/fasterRcnnResnet50v1.tar.gz --strip-components 2 --directory source_dir/checkpoint faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/checkpoint/

faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/checkpoint/ckpt-0.data-00000-of-00001
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/checkpoint/checkpoint
faster_rcnn_resnet50_v1_640x640_coco17_tpu-8/checkpoint/ckpt-0.index


# Editing pipeline.config file for Faster R-CNN ResNet50 V1 640x640

In [65]:
# not many changes except the model, batch size kept at 8

In [66]:
tensorboard_output_config = sagemaker.debugger.TensorBoardOutputConfig(
    s3_output_path=tensorboard_s3_prefix,
    container_local_output_path='/opt/training/'
)

estimator = CustomFramework(
    role=role,
    image_uri=container,
    entry_point='run_training.sh',
    source_dir='source_dir/',
    hyperparameters={
        "model_dir": "/opt/training",        
        "pipeline_config_path": "pipeline.config",
        "num_train_steps": "2000",    
        "sample_1_of_n_eval_examples": "1"
    },
    instance_count=1,
    instance_type='ml.g5.xlarge',
    tensorboard_output_config=tensorboard_output_config,
    disable_profiler=True,
    base_job_name='tf2-object-detection'
)

estimator.fit(inputs)

INFO:sagemaker:Creating training-job with name: tf2-object-detection-2024-09-07-06-21-50-014


2024-09-07 06:21:59 Starting - Starting the training job...
2024-09-07 06:22:12 Starting - Preparing the instances for training...
2024-09-07 06:23:01 Downloading - Downloading the training image...............
2024-09-07 06:25:32 Training - Training image download completed. Training in progress....2024-09-07 06:25:46,718 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 06:25:46,754 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 06:25:46,789 sagemaker-training-toolkit INFO     No Neurons detected (normal if no neurons installed)
2024-09-07 06:25:46,804 sagemaker-training-toolkit INFO     Invoking user script
Training Env:
{
    "additional_framework_parameters": {},
    "channel_input_dirs": {
        "train": "/opt/ml/input/data/train",
        "val": "/opt/ml/input/data/val"
    },
    "current_host": "algo-1",
    "current_instance_group": "homogeneousCluster",
    "current_insta

Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
W0907 06:25:59.655544 140450077964096 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: sparse_to_dense (from tensorflow.python.ops.sparse_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
Instructions for updating:
Use `tf.cast` instead.
W0907 06:26:03.320470 140450077964096 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: to_float (from tensorflow.python.ops.math_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.cast` instead.
/usr/local/lib/python3.8/dist-packages/keras/src/backend.py:452: UserWarning: `tf.keras.backend.set_learning_phase` is deprecated and will be removed after 2020-10-11. To update it, simply pass a True/Fa

INFO:tensorflow:Step 200 per-step time 0.344s
I0907 06:29:11.049438 140450077964096 model_lib_v2.py:705] Step 200 per-step time 0.344s
INFO:tensorflow:{'Loss/BoxClassifierLoss/classification_loss': 0.23867312,
 'Loss/BoxClassifierLoss/localization_loss': 0.53392774,
 'Loss/RPNLoss/localization_loss': 0.37988535,
 'Loss/RPNLoss/objectness_loss': 0.051797174,
 'Loss/regularization_loss': 0.0,
 'Loss/total_loss': 1.2042834,
 'learning_rate': 0.0159997}
I0907 06:29:11.049696 140450077964096 model_lib_v2.py:708] {'Loss/BoxClassifierLoss/classification_loss': 0.23867312,
 'Loss/BoxClassifierLoss/localization_loss': 0.53392774,
 'Loss/RPNLoss/localization_loss': 0.37988535,
 'Loss/RPNLoss/objectness_loss': 0.051797174,
 'Loss/regularization_loss': 0.0,
 'Loss/total_loss': 1.2042834,
 'learning_rate': 0.0159997}
INFO:tensorflow:Step 300 per-step time 0.346s
I0907 06:29:45.675330 140450077964096 model_lib_v2.py:705] Step 300 per-step time 0.346s
INFO:tensorflow:{'Loss/BoxClassifierLoss/classifi

INFO:tensorflow:Step 1200 per-step time 0.346s
I0907 06:34:56.898859 140450077964096 model_lib_v2.py:705] Step 1200 per-step time 0.346s
INFO:tensorflow:{'Loss/BoxClassifierLoss/classification_loss': 0.1879625,
 'Loss/BoxClassifierLoss/localization_loss': 0.42928898,
 'Loss/RPNLoss/localization_loss': 0.37040818,
 'Loss/RPNLoss/objectness_loss': 0.051516943,
 'Loss/regularization_loss': 0.0,
 'Loss/total_loss': 1.0391766,
 'learning_rate': 0.0293332}
I0907 06:34:56.899130 140450077964096 model_lib_v2.py:708] {'Loss/BoxClassifierLoss/classification_loss': 0.1879625,
 'Loss/BoxClassifierLoss/localization_loss': 0.42928898,
 'Loss/RPNLoss/localization_loss': 0.37040818,
 'Loss/RPNLoss/objectness_loss': 0.051516943,
 'Loss/regularization_loss': 0.0,
 'Loss/total_loss': 1.0391766,
 'learning_rate': 0.0293332}
INFO:tensorflow:Step 1300 per-step time 0.346s
I0907 06:35:31.525145 140450077964096 model_lib_v2.py:705] Step 1300 per-step time 0.346s
INFO:tensorflow:{'Loss/BoxClassifierLoss/classi

Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
W0907 06:39:45.592698 140109870597952 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: sparse_to_dense (from tensorflow.python.ops.sparse_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
Instructions for updating:
Use `tf.cast` instead.
W0907 06:39:46.838816 140109870597952 deprecation.py:364] From /usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1176: to_float (from tensorflow.python.ops.math_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.cast` instead.
INFO:tensorflow:Waiting for new checkpoint at /opt/training
I0907 06:39:49.171358 140109870597952 checkpoint_utils.py:168] Waiting for new checkpoint at /opt/training
INFO:tensorflow:Found new checkpoint

INFO:tensorflow:Waiting for new checkpoint at /opt/training
I0907 06:44:49.272055 140109870597952 checkpoint_utils.py:168] Waiting for new checkpoint at /opt/training
INFO:tensorflow:Timed-out waiting for a checkpoint.
I0907 06:44:58.285762 140109870597952 checkpoint_utils.py:231] Timed-out waiting for a checkpoint.
creating index...
index created!
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=13.23s).
Accumulating evaluation results...
DONE (t=0.37s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=100 ] = 0.071
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=100 ] = 0.161
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=100 ] = 0.060
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=100 ] = 0.024
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=100 ] = 0.249
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= large | maxDets=100 ] = 0.309
 Ave